In [ ]:
import ee
import geemap

In [ ]:
ee.Authenticate()
ee.Initialize(project="vaibhav-gee")

In [ ]:
Taluka = ee.FeatureCollection("projects/vaibhav-gee/assets/EX1-2/BOUNDARY")

In [ ]:
map = geemap.Map()
map

Map(center=[0, 0], controls=(WidgetControl(options=['position', 'transparent_bg'], widget=SearchDataGUI(childr…

In [ ]:
def scale_landsat(image):
  optical = image.select(['SR_B1','SR_B2','SR_B3','SR_B4','SR_B5','SR_B6','SR_B7']).multiply(0.0000275).add(-0.2)
  return image.addBands(optical, overwrite=True)

In [ ]:
Landsat9 = ee.ImageCollection("LANDSAT/LC09/C02/T1_L2")
L9_Optical = Landsat9.select('SR_B1','SR_B2','SR_B3','SR_B4','SR_B5','SR_B6','SR_B7')
ROI = L9_Optical.filterBounds(Taluka).filterDate("2025-01-01","2025-05-30").filterMetadata('CLOUD_COVER','less_than',10).mean().clip(Taluka)
scaled_L9 = scale_landsat(ROI)
vis_2025_L9_TCC = {'bands': ['SR_B4', 'SR_B3', 'SR_B2'], 'gamma': 1.0, 'min': 8210.6, 'max': 12514.4}
vis_2025_L9_FCC = {'bands': ['SR_B5', 'SR_B4', 'SR_B3'], 'gamma': 1.0, 'min': 8211.0, 'max': 17395.0}
map.addLayer(ROI,vis_2025_L9_TCC,'2025_TCC')
map.addLayer(ROI,vis_2025_L9_FCC,"2025_FCC")
map

Map(bottom=117622.0, center=[18.54992849796143, 73.87111316609383], controls=(WidgetControl(options=['position…

# **NDVI** (VEGETATION INDEX) = (B5-B4)/(B5+B4)

In [ ]:
NIR = scaled_L9.select("SR_B5")
RED = scaled_L9.select("SR_B4")

In [ ]:
NDVI = NIR.subtract(RED).divide(NIR.add(RED)).rename("NDVI")
vis_NDVI = {'bands': ['NDVI'], 'palette': ['#a50026', '#a70226', '#a90426', '#ab0626', '#ad0826', '#af0926', '#b10b26', '#b30d26', '#b50f26', '#b71126', '#b91326', '#bb1526', '#bd1726', '#be1827', '#c01a27', '#c21c27', '#c41e27', '#c62027', '#c82227', '#ca2427', '#cc2627', '#ce2827', '#d02927', '#d22b27', '#d42d27', '#d62f27', '#d83128', '#d93429', '#da362a', '#db382b', '#dc3b2c', '#dd3d2d', '#de402e', '#e0422f', '#e14430', '#e24731', '#e34933', '#e44c34', '#e54e35', '#e65036', '#e75337', '#e95538', '#ea5739', '#eb5a3a', '#ec5c3b', '#ed5f3c', '#ee613e', '#ef633f', '#f16640', '#f26841', '#f36b42', '#f46d43', '#f47044', '#f57245', '#f57547', '#f57748', '#f67a49', '#f67c4a', '#f67f4b', '#f7814c', '#f7844e', '#f8864f', '#f88950', '#f88c51', '#f98e52', '#f99153', '#f99355', '#fa9656', '#fa9857', '#fa9b58', '#fb9d59', '#fba05b', '#fba35c', '#fca55d', '#fca85e', '#fcaa5f', '#fdad60', '#fdaf62', '#fdb163', '#fdb365', '#fdb567', '#fdb768', '#fdb96a', '#fdbb6c', '#fdbd6d', '#fdbf6f', '#fdc171', '#fdc372', '#fdc574', '#fdc776', '#fec877', '#feca79', '#fecc7b', '#fece7c', '#fed07e', '#fed27f', '#fed481', '#fed683', '#fed884', '#feda86', '#fedc88', '#fede89', '#fee08b', '#fee18d', '#fee28f', '#fee491', '#fee593', '#fee695', '#fee797', '#fee999', '#feea9b', '#feeb9d', '#feec9f', '#feeda1', '#feefa3', '#fff0a6', '#fff1a8', '#fff2aa', '#fff3ac', '#fff5ae', '#fff6b0', '#fff7b2', '#fff8b4', '#fffab6', '#fffbb8', '#fffcba', '#fffdbc', '#fffebe', '#feffbe', '#fdfebc', '#fbfdba', '#fafdb8', '#f8fcb6', '#f7fcb4', '#f5fbb2', '#f4fab0', '#f2faae', '#f1f9ac', '#eff8aa', '#eef8a8', '#ecf7a6', '#ebf7a3', '#e9f6a1', '#e8f59f', '#e6f59d', '#e5f49b', '#e3f399', '#e2f397', '#e0f295', '#dff293', '#ddf191', '#dcf08f', '#daf08d', '#d9ef8b', '#d7ee8a', '#d5ed88', '#d3ec87', '#d1ec86', '#cfeb85', '#cdea83', '#cbe982', '#c9e881', '#c7e77f', '#c5e67e', '#c3e67d', '#c1e57b', '#bfe47a', '#bde379', '#bbe278', '#b9e176', '#b7e075', '#b5df74', '#b3df72', '#b1de71', '#afdd70', '#addc6f', '#abdb6d', '#a9da6c', '#a7d96b', '#a5d86a', '#a2d76a', '#a0d669', '#9dd569', '#9bd469', '#98d368', '#96d268', '#93d168', '#91d068', '#8ecf67', '#8ccd67', '#89cc67', '#87cb67', '#84ca66', '#82c966', '#7fc866', '#7dc765', '#7ac665', '#78c565', '#75c465', '#73c264', '#70c164', '#6ec064', '#6bbf64', '#69be63', '#66bd63', '#63bc62', '#60ba62', '#5db961', '#5ab760', '#57b65f', '#54b45f', '#51b35e', '#4eb15d', '#4bb05c', '#48ae5c', '#45ad5b', '#42ac5a', '#3faa59', '#3ca959', '#39a758', '#36a657', '#33a456', '#30a356', '#2da155', '#2aa054', '#279f53', '#249d53', '#219c52', '#1e9a51', '#1b9950', '#199750', '#18954f', '#17934e', '#16914d', '#15904c', '#148e4b', '#138c4a', '#128a49', '#118848', '#108647', '#0f8446', '#0e8245', '#0d8044', '#0c7f43', '#0b7d42', '#0a7b41', '#097940', '#08773f', '#07753e', '#06733d', '#05713c', '#04703b', '#036e3a', '#026c39', '#016a38', '#006837'], 'min': 0.012239987203649631, 'max': 0.6933424090265883}
map.addLayer(NDVI,vis_NDVI,"NDVI_2025")
map

Map(bottom=117622.0, center=[18.54992849796143, 73.87111316609383], controls=(WidgetControl(options=['position…

**NDVI RECLASSIFICATION**

-  < O.2 = NO VEGETATION

-  0.21 - 0.5 = MODERATE VEGETATION

- > 0.5 = DENSE VEGETATION

In [ ]:
NDVI_RECLASS = (NDVI
               .where(NDVI.gte(0.2),1)
               .where(NDVI.gte(0.21).And(NDVI.lt(0.5)),2)
               .where(NDVI.gte(0.5),3)
              )
vis_NDVI_RECLASS = {'bands': ['NDVI'], 'palette': ['#a50026', '#a70226', '#a90426', '#ab0626', '#ad0826', '#af0926', '#b10b26', '#b30d26', '#b50f26', '#b71126', '#b91326', '#bb1526', '#bd1726', '#be1827', '#c01a27', '#c21c27', '#c41e27', '#c62027', '#c82227', '#ca2427', '#cc2627', '#ce2827', '#d02927', '#d22b27', '#d42d27', '#d62f27', '#d83128', '#d93429', '#da362a', '#db382b', '#dc3b2c', '#dd3d2d', '#de402e', '#e0422f', '#e14430', '#e24731', '#e34933', '#e44c34', '#e54e35', '#e65036', '#e75337', '#e95538', '#ea5739', '#eb5a3a', '#ec5c3b', '#ed5f3c', '#ee613e', '#ef633f', '#f16640', '#f26841', '#f36b42', '#f46d43', '#f47044', '#f57245', '#f57547', '#f57748', '#f67a49', '#f67c4a', '#f67f4b', '#f7814c', '#f7844e', '#f8864f', '#f88950', '#f88c51', '#f98e52', '#f99153', '#f99355', '#fa9656', '#fa9857', '#fa9b58', '#fb9d59', '#fba05b', '#fba35c', '#fca55d', '#fca85e', '#fcaa5f', '#fdad60', '#fdaf62', '#fdb163', '#fdb365', '#fdb567', '#fdb768', '#fdb96a', '#fdbb6c', '#fdbd6d', '#fdbf6f', '#fdc171', '#fdc372', '#fdc574', '#fdc776', '#fec877', '#feca79', '#fecc7b', '#fece7c', '#fed07e', '#fed27f', '#fed481', '#fed683', '#fed884', '#feda86', '#fedc88', '#fede89', '#fee08b', '#fee18d', '#fee28f', '#fee491', '#fee593', '#fee695', '#fee797', '#fee999', '#feea9b', '#feeb9d', '#feec9f', '#feeda1', '#feefa3', '#fff0a6', '#fff1a8', '#fff2aa', '#fff3ac', '#fff5ae', '#fff6b0', '#fff7b2', '#fff8b4', '#fffab6', '#fffbb8', '#fffcba', '#fffdbc', '#fffebe', '#feffbe', '#fdfebc', '#fbfdba', '#fafdb8', '#f8fcb6', '#f7fcb4', '#f5fbb2', '#f4fab0', '#f2faae', '#f1f9ac', '#eff8aa', '#eef8a8', '#ecf7a6', '#ebf7a3', '#e9f6a1', '#e8f59f', '#e6f59d', '#e5f49b', '#e3f399', '#e2f397', '#e0f295', '#dff293', '#ddf191', '#dcf08f', '#daf08d', '#d9ef8b', '#d7ee8a', '#d5ed88', '#d3ec87', '#d1ec86', '#cfeb85', '#cdea83', '#cbe982', '#c9e881', '#c7e77f', '#c5e67e', '#c3e67d', '#c1e57b', '#bfe47a', '#bde379', '#bbe278', '#b9e176', '#b7e075', '#b5df74', '#b3df72', '#b1de71', '#afdd70', '#addc6f', '#abdb6d', '#a9da6c', '#a7d96b', '#a5d86a', '#a2d76a', '#a0d669', '#9dd569', '#9bd469', '#98d368', '#96d268', '#93d168', '#91d068', '#8ecf67', '#8ccd67', '#89cc67', '#87cb67', '#84ca66', '#82c966', '#7fc866', '#7dc765', '#7ac665', '#78c565', '#75c465', '#73c264', '#70c164', '#6ec064', '#6bbf64', '#69be63', '#66bd63', '#63bc62', '#60ba62', '#5db961', '#5ab760', '#57b65f', '#54b45f', '#51b35e', '#4eb15d', '#4bb05c', '#48ae5c', '#45ad5b', '#42ac5a', '#3faa59', '#3ca959', '#39a758', '#36a657', '#33a456', '#30a356', '#2da155', '#2aa054', '#279f53', '#249d53', '#219c52', '#1e9a51', '#1b9950', '#199750', '#18954f', '#17934e', '#16914d', '#15904c', '#148e4b', '#138c4a', '#128a49', '#118848', '#108647', '#0f8446', '#0e8245', '#0d8044', '#0c7f43', '#0b7d42', '#0a7b41', '#097940', '#08773f', '#07753e', '#06733d', '#05713c', '#04703b', '#036e3a', '#026c39', '#016a38', '#006837'], 'min': 0.08491550177341939, 'max': 3.0}
map.addLayer(NDVI_RECLASS,vis_NDVI_RECLASS,"NDVI_RECLASS")
map

Map(bottom=117622.0, center=[18.54992849796143, 73.87111316609383], controls=(WidgetControl(options=['position…

In [ ]:
geemap.ee_export_image(NDVI, filename='NDVI.tif', scale=30, region=Taluka.geometry())

Generating URL ...
Please wait ...
Data downloaded to /content/NDVI.tif


In [ ]:
map.save("NDVI.html")
from google.colab import files
files.download("NDVI.html")

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

# SAVI = (SOIL ADJUSTED VEGETATION INDEX)
(NIR-R/NIR+R+L)(1L)

In [ ]:
SAVI = ((NIR.subtract(RED)).divide(NIR.add(RED).add(0.5))).multiply(1.5).rename("SAVI")
vis_SAVI = {'bands': ['SAVI'], 'palette': ['#543005', '#563105', '#583305', '#5b3406', '#5d3506', '#5f3606', '#613806', '#633906', '#663a07', '#683c07', '#6a3d07', '#6c3e07', '#6e4007', '#714108', '#734208', '#754308', '#774508', '#794608', '#7c4709', '#7e4909', '#804a09', '#824b09', '#844c09', '#874e0a', '#894f0a', '#8b500a', '#8d520b', '#8f540c', '#91560d', '#93580f', '#955910', '#975b12', '#995d13', '#9b5f14', '#9d6116', '#9f6317', '#a16518', '#a3671a', '#a5691b', '#a76a1d', '#a96c1e', '#ab6e1f', '#ad7021', '#af7222', '#b17423', '#b37625', '#b57826', '#b77928', '#b97b29', '#bb7d2a', '#bd7f2c', '#bf812d', '#c08430', '#c28633', '#c38936', '#c48b3a', '#c58e3d', '#c79040', '#c89343', '#c99546', '#ca9849', '#cc9a4c', '#cd9d50', '#cea053', '#cfa256', '#d1a559', '#d2a75c', '#d3aa5f', '#d4ac62', '#d6af65', '#d7b169', '#d8b46c', '#d9b76f', '#dbb972', '#dcbc75', '#ddbe78', '#dec17b', '#dfc37e', '#e0c481', '#e1c684', '#e2c787', '#e3c989', '#e4ca8c', '#e5cc8f', '#e6cd92', '#e7cf94', '#e8d097', '#e8d29a', '#e9d39d', '#ead59f', '#ebd6a2', '#ecd8a5', '#edd9a8', '#eedbaa', '#efdcad', '#f0deb0', '#f1dfb3', '#f1e1b5', '#f2e2b8', '#f3e4bb', '#f4e5be', '#f5e7c0', '#f6e8c3', '#f6e9c5', '#f6e9c7', '#f6eac9', '#f6eacb', '#f6ebcd', '#f6ebcf', '#f6ecd1', '#f6ecd3', '#f6edd5', '#f6edd7', '#f6eed9', '#f6eedb', '#f5efdc', '#f5efde', '#f5f0e0', '#f5f0e2', '#f5f1e4', '#f5f1e6', '#f5f2e8', '#f5f2ea', '#f5f3ec', '#f5f3ee', '#f5f4f0', '#f5f4f2', '#f5f5f4', '#f4f5f5', '#f2f4f4', '#f0f4f3', '#eff3f3', '#edf3f2', '#ebf3f2', '#e9f2f1', '#e7f2f0', '#e6f1f0', '#e4f1ef', '#e2f0ee', '#e0f0ee', '#def0ed', '#ddefed', '#dbefec', '#d9eeeb', '#d7eeeb', '#d5edea', '#d4ede9', '#d2ede9', '#d0ece8', '#ceece8', '#ccebe7', '#cbebe6', '#c9eae6', '#c7eae5', '#c4e9e4', '#c1e8e2', '#bfe7e1', '#bce5df', '#b9e4de', '#b6e3dd', '#b4e2db', '#b1e1da', '#aee0d8', '#abdfd7', '#a8ddd5', '#a6dcd4', '#a3dbd3', '#a0dad1', '#9dd9d0', '#9ad8ce', '#98d7cd', '#95d6cc', '#92d4ca', '#8fd3c9', '#8dd2c7', '#8ad1c6', '#87d0c5', '#84cfc3', '#81cec2', '#7fccc0', '#7ccabe', '#79c8bc', '#76c6ba', '#73c3b8', '#70c1b6', '#6dbfb4', '#6abdb2', '#67bbb0', '#64b9ae', '#61b7ac', '#5eb5aa', '#5bb3a8', '#58b0a7', '#55aea5', '#52aca3', '#4faaa1', '#4da89f', '#4aa69d', '#47a49b', '#44a299', '#419f97', '#3e9d95', '#3b9b93', '#389991', '#35978f', '#33958d', '#31938b', '#2f9189', '#2d8f87', '#2b8d85', '#298b83', '#278a82', '#258880', '#23867e', '#21847c', '#1f827a', '#1d8078', '#1a7e76', '#187c74', '#167a72', '#147870', '#12766e', '#10746c', '#0e726a', '#0c7169', '#0a6f67', '#086d65', '#066b63', '#046961', '#02675f', '#01655d', '#01645b', '#016259', '#016058', '#015f56', '#015d54', '#015b52', '#015a50', '#01584f', '#01564d', '#01554b', '#015349', '#015147', '#005046', '#004e44', '#004c42', '#004b40', '#00493e', '#00483d', '#00463b', '#004439', '#004337', '#004135', '#003f34', '#003e32', '#003c30'], 'min': 0.019248912829940613, 'max': 0.3767024021533255}
map.addLayer(SAVI,vis_SAVI,"SAVI")
map

Map(bottom=117622.0, center=[18.54992849796143, 73.87111316609383], controls=(WidgetControl(options=['position…

In [ ]:
geemap.ee_export_image(SAVI, filename='SAVI.tif', scale=30, region=Taluka.geometry())

Generating URL ...
Please wait ...
Data downloaded to /content/SAVI.tif


In [ ]:
map.save("SAVI.html")
from google.colab import files
files.download("SAVI.html")

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

#NDWI (WATER INDEX) = (B3-B5)/(B3+B5)

In [ ]:
B3 = scaled_L9.select("SR_B3")
B5 = scaled_L9.select("SR_B5")

In [ ]:
NDWI = (B3.subtract(B5)).divide(B3.add(B5))
vis_NDWI = {'bands': ['SR_B3'], 'palette': ['#f7fbff', '#f6faff', '#f5fafe', '#f5f9fe', '#f4f9fe', '#f3f8fe', '#f2f8fd', '#f2f7fd', '#f1f7fd', '#f0f6fd', '#eff6fc', '#eef5fc', '#eef5fc', '#edf4fc', '#ecf4fb', '#ebf3fb', '#eaf3fb', '#eaf2fb', '#e9f2fa', '#e8f1fa', '#e7f1fa', '#e7f0fa', '#e6f0f9', '#e5eff9', '#e4eff9', '#e3eef9', '#e3eef8', '#e2edf8', '#e1edf8', '#e0ecf8', '#dfecf7', '#dfebf7', '#deebf7', '#ddeaf7', '#dceaf6', '#dce9f6', '#dbe9f6', '#dae8f6', '#d9e8f5', '#d9e7f5', '#d8e7f5', '#d7e6f5', '#d6e6f4', '#d6e5f4', '#d5e5f4', '#d4e4f4', '#d3e4f3', '#d3e3f3', '#d2e3f3', '#d1e2f3', '#d0e2f2', '#d0e1f2', '#cfe1f2', '#cee0f2', '#cde0f1', '#cddff1', '#ccdff1', '#cbdef1', '#cadef0', '#caddf0', '#c9ddf0', '#c8dcf0', '#c7dcef', '#c7dbef', '#c6dbef', '#c4daee', '#c3daee', '#c2d9ee', '#c1d9ed', '#bfd8ed', '#bed8ec', '#bdd7ec', '#bcd7eb', '#bad6eb', '#b9d6ea', '#b8d5ea', '#b7d4ea', '#b5d4e9', '#b4d3e9', '#b3d3e8', '#b2d2e8', '#b0d2e7', '#afd1e7', '#aed1e7', '#add0e6', '#abd0e6', '#aacfe5', '#a9cfe5', '#a8cee4', '#a6cee4', '#a5cde3', '#a4cce3', '#a3cce3', '#a1cbe2', '#a0cbe2', '#9fcae1', '#9dcae1', '#9cc9e1', '#9ac8e0', '#99c7e0', '#97c6df', '#95c5df', '#94c4df', '#92c4de', '#91c3de', '#8fc2de', '#8dc1dd', '#8cc0dd', '#8abfdd', '#89bedc', '#87bddc', '#85bcdc', '#84bcdb', '#82bbdb', '#81badb', '#7fb9da', '#7db8da', '#7cb7da', '#7ab6d9', '#79b5d9', '#77b5d9', '#75b4d8', '#74b3d8', '#72b2d8', '#71b1d7', '#6fb0d7', '#6dafd7', '#6caed6', '#6aaed6', '#69add5', '#68acd5', '#66abd4', '#65aad4', '#64a9d3', '#63a8d3', '#61a7d2', '#60a7d2', '#5fa6d1', '#5da5d1', '#5ca4d0', '#5ba3d0', '#5aa2cf', '#58a1cf', '#57a0ce', '#56a0ce', '#549fcd', '#539ecd', '#529dcc', '#519ccc', '#4f9bcb', '#4e9acb', '#4d99ca', '#4b98ca', '#4a98c9', '#4997c9', '#4896c8', '#4695c8', '#4594c7', '#4493c7', '#4292c6', '#4191c6', '#4090c5', '#3f8fc5', '#3e8ec4', '#3d8dc4', '#3c8cc3', '#3b8bc2', '#3a8ac2', '#3989c1', '#3888c1', '#3787c0', '#3686c0', '#3585bf', '#3484bf', '#3383be', '#3282be', '#3181bd', '#3080bd', '#2f7fbc', '#2e7ebc', '#2d7dbb', '#2c7cba', '#2b7bba', '#2a7ab9', '#2979b9', '#2777b8', '#2676b8', '#2575b7', '#2474b7', '#2373b6', '#2272b6', '#2171b5', '#2070b4', '#206fb4', '#1f6eb3', '#1e6db2', '#1d6cb1', '#1c6bb0', '#1c6ab0', '#1b69af', '#1a68ae', '#1967ad', '#1966ad', '#1865ac', '#1764ab', '#1663aa', '#1562a9', '#1561a9', '#1460a8', '#135fa7', '#125ea6', '#125da6', '#115ca5', '#105ba4', '#0f5aa3', '#0e59a2', '#0e58a2', '#0d57a1', '#0c56a0', '#0b559f', '#0a549e', '#0a539e', '#09529d', '#08519c', '#08509b', '#084f99', '#084e98', '#084d96', '#084c95', '#084b93', '#084a91', '#084990', '#08488e', '#08478d', '#08468b', '#08458a', '#084488', '#084387', '#084285', '#084184', '#084082', '#083e81', '#083d7f', '#083c7d', '#083b7c', '#083a7a', '#083979', '#083877', '#083776', '#083674', '#083573', '#083471', '#083370', '#08326e', '#08316d', '#08306b'], 'min': -0.6491521819722192, 'max': 0.1638846449482344}
map.addLayer(NDWI,vis_NDWI,"NDWI")
map

Map(bottom=117622.0, center=[18.54992849796143, 73.87111316609383], controls=(WidgetControl(options=['position…

In [ ]:
geemap.ee_export_image(NDWI, filename='NDWI.tif', scale=30, region=Taluka.geometry())

Generating URL ...
Please wait ...
Data downloaded to /content/NDWI.tif


In [ ]:
map.save("NDWI.html")
from google.colab import files
files.download("NDWI.html")

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

#NDMI (MOISTURE INDEX) = (5-6)/(5+6)

5 = NIR

6 = SWIR

In [ ]:
SWIR = scaled_L9.select("SR_B6")
NIR = scaled_L9.select("SR_B5")

In [ ]:
NDMI = (NIR.subtract(SWIR)).divide(NIR.add(SWIR))
vis_NDMI = {'bands': ['SR_B5'], 'palette': ['#a50026', '#d22c27', '#ef623e', '#fb9c59', '#fece7c', '#fff1a7', '#eef8a7', '#c6e77f', '#95d168', '#58b660', '#18944e', '#006837'], 'min': -0.15106640106732505, 'max': 0.29346047096061006}
map.addLayer(NDMI,vis_NDMI,"NDMI")
map

Map(bottom=117622.0, center=[18.54992849796143, 73.87111316609383], controls=(WidgetControl(options=['position…

In [ ]:
geemap.ee_export_image(NDMI, filename='NDMI_Corrected.tif', scale=30, region=Taluka.geometry())

Generating URL ...
Please wait ...
Data downloaded to /content/NDMI_Corrected.tif


In [ ]:
map.save("NDMI_Corrected.html")
from google.colab import files
files.download("NDMI_Corrected.html")

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

#NDBI (BUILTUP INDEX) = (6-5)/(6+5)

5 = NIR

6 = SWIR

In [ ]:
NDBI = (SWIR.subtract(NIR)).divide(SWIR.add(NIR)).rename("NDBI")
vis_NDBI = {'bands': ['NDBI'], 'palette': ['#00a600', '#ffff66', '#ffa500', '#ff4500', '#8b0000'], 'min': -0.29346047096061006, 'max': 0.15106640106732505}
map.addLayer(NDBI,vis_NDBI,"NDBI")
map

Map(bottom=117622.0, center=[18.54992849796143, 73.87111316609383], controls=(WidgetControl(options=['position…

In [ ]:
geemap.ee_export_image(NDBI, filename='NDBI_Corrected.tif', scale=30, region=Taluka.geometry())

Generating URL ...
Please wait ...
Data downloaded to /content/NDBI_Corrected.tif


In [ ]:
map.save("NDBI_Corrected.html")
from google.colab import files
files.download("NDBI_Corrected.html")

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>